In [1]:
# 1. Install chrome driver here: https://chromedriver.chromium.org/downloads. Replace the chrome_driver_path
#    in the cell below with the path to your chrome driver
# 2. Run this cell. you will probably (definitely) have to download some python libraries. Go to your terminal 
#    and type 'pip install [package name here]' for whatever your missing. I'd guess you will need to install 
#    bs4 and selenium. If you have used python on your machine before you will probably have pip which is just
#    a package manager for python. If you do not, text me. 
# 3. Run cells 3 and 4. They won't do anything but you will be able to call the functions in them. 
# 4. Run the 5th cell that says 'df = scrape('2019-20')'. It will only scrape 2 pages.
# 5. Run the 6th cell which will give you a preview of the data. Verify that it is correct by looking at the 
#    nba.com data. Here is the link: https://stats.nba.com/players/boxscores-advanced/?Season=2019-20&SeasonType=Regular%20Season
# 6. If all looks good, delete the if statement in the scrape function (I have a comment by it) so it won't stop
#    after 5 iterations. Rerun that cell. 
# 7. Run the cell that loops over the years. Sit back and relax - check on it every once and awhile. It'll print the
#    count after every page it has scraped and each season should have upwards of 40.
import numpy as np
import pandas as pd
import datetime
from bs4 import BeautifulSoup
from selenium import webdriver

In [2]:
chrome_driver_path = '/Users/danielsmith/Downloads/chromedriver' # DOWNLOAD CHROME DRIVER, REPLACE W YOUR PATH 
browser = webdriver.Chrome(executable_path = chrome_driver_path)
base_url = 'https://stats.nba.com/teams/boxscores-scoring/?Season='
end_url = '&SeasonType=Regular%20Season'

In [3]:
# convert attrbs to int
def to_int(num) :
    try :
        return int(num)
    except :
        return num

# convert attrbs to float
def to_float(num) :
    try :
        return float(num)
    except :
        return num

In [17]:
def check_page(browser) :
    table = browser.find_element_by_class_name('nba-stat-table__overflow')
    if table == None :
        return False
    return table

def get_next_page(browser) :
    browser.find_element_by_class_name('stats-table-pagination__next').click()
    return check_page(browser)

def scrape(season) :
    url = base_url + season + end_url
    browser.get(url)
    browser.implicitly_wait(100)
    players = []
    table = check_page(browser)
    count = 0
    prev = ''
    while table is not None : 
        name = ''
        lines = table.text.split('\n')
        if prev == lines[16] :
            break
        prev = lines[16]
        for idx, stats in enumerate(lines):
            print(stats)
            if idx < 16 :
                continue
            #elif idx % 2 == 1 :
             #   team = stats
            else :
                arr = stats.split(' ')
                print(arr)
                matchup = arr[1] + arr[2] + arr[3]
                player = {'TEAM':arr[0], 'MATCH UP':matchup, 'GAME DATE':arr[4],
                          'W/L':arr[5], 'MIN':to_int(arr[6]), '%FGA 2PT':to_float(arr[7]), 
                          '%FGA 3PT':to_float(arr[8]), '%PTS 2PT':to_float(arr[9]), '%PTS 2PT MR':to_float(arr[10]), 
                          '%PTS 3PT':to_float(arr[11]), '%PTS FBPS':to_float(arr[12]), '%PTS FT':to_float(arr[13]),
                          '%PTS PTS OFF TO':to_float(arr[14]), '%PTS PITP':to_float(arr[15]), 
                          '2FGM %AST':to_float(arr[16]),'2FGM UAST%':to_float(arr[17]), 
                          '3FGM %AST':to_float(arr[18]), '3FGM %UAST':to_float(arr[19]), 
                          'FGM %AST':to_float(arr[20]), 'FGM %UAST':to_float(arr[21]) } 
                players.append(player)
        count += 1
      #  if count > 2:
       #     break
        print(count)
        table = get_next_page(browser)
    return pd.DataFrame(players)

In [15]:
# run this once to make sure no errors thrown
df = scrape('2019-20')

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
PHI PHI vs. DET 03/11/2020 W 48 60.2 39.8 45.2 6.5 33.9 8.9 21.0 10.5 38.7 53.6 46.4 92.9 7.1 66.7 33.3
['PHI', 'PHI', 'vs.', 'DET', '03/11/2020', 'W', '48', '60.2', '39.8', '45.2', '6.5', '33.9', '8.9', '21.0', '10.5', '38.7', '53.6', '46.4', '92.9', '7.1', '66.7', '33.3']
ATL ATL vs. NYK 03/11/2020 L 53 61.3 38.7 51.9 7.6 32.1 9.2 16.0 8.4 44.3 47.1 52.9 71.4 28.6 54.2 45.8
['ATL', 'ATL', 'vs.', 'NYK', '03/11/2020', 'L', '53', '61.3', '38.7', '51.9', '7.6', '32.1', '9.2', '16.0', '8.4', '44.3', '47.1', '52.9', '71.4', '28.6', '54.2', '45.8']
DAL DAL vs. DEN 03/11/2020 W 48 62.0 38.0 53.1 0.0 31.9 12.4 15.0 24.8 53.1 46.7 53.3 75.0 25.0 54.8 45.2
['DAL', 'DAL', 'vs.', 'DEN', '03/11/2020', 'W', '48', '62.0', '38.0', '53.1', '0.0', '31.9', '12.4', '15.0', '24.8', '53.1', '46.7', '53.3', '75.0', '25.0', '54.8'

In [16]:
df.head()

TEAM   MATCH UP   GAME DATE W/L  MIN  %FGA 2PT  %FGA 3PT  %PTS 2PT  \
0  PHI  PHIvs.DET  03/11/2020   W   48      60.2      39.8      45.2   
1  ATL  ATLvs.NYK  03/11/2020   L   53      61.3      38.7      51.9   
2  DAL  DALvs.DEN  03/11/2020   W   48      62.0      38.0      53.1   
3  DEN    DEN@DAL  03/11/2020   L   48      53.0      47.0      51.5   
4  NYK    NYK@ATL  03/11/2020   W   53      70.2      29.8      57.4   

   %PTS 2PT MR  %PTS 3PT  %PTS FBPS  %PTS FT  %PTS PTS OFF TO  %PTS PITP  \
0          6.5      33.9        8.9     21.0             10.5       38.7   
1          7.6      32.1        9.2     16.0              8.4       44.3   
2          0.0      31.9       12.4     15.0             24.8       53.1   
3         12.4      43.3       20.6      5.2              2.1       39.2   
4         11.8      24.3       21.3     18.4             19.1       45.6   

   2FGM %AST  2FGM UAST%  3FGM %AST  3FGM %UAST  FGM %AST  FGM %UAST  
0       53.6        46.4       92.9         7.1      66.7       33.3  
1       47.1        52.9       71.4        28.6      54.2       45.8  
2       46.7        53.3       75.0        25.0      54.8       45.2  
3       48.0        52.0       78.6        21.4      59.0       41.0  
4       59.0        41.0       81.8        18.2      64.0       36.0

In [18]:
yrs = ['2014-15', '2015-16', '2016-17', '2017-18','2018-19', '2019-20']
for yr in yrs : 
    df = scrape(yr)
    csv = 'teams_scoring_' + str(yr) + '.csv'
    df.to_csv(csv, index=False)

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
DAL DAL vs. POR 04/15/2015 W 48 70.9 29.1 52.6 8.8 23.7 21.9 23.7 13.2 43.9 36.7 63.3 77.8 22.2 46.2 53.8
['DAL', 'DAL', 'vs.', 'POR', '04/15/2015', 'W', '48', '70.9', '29.1', '52.6', '8.8', '23.7', '21.9', '23.7', '13.2', '43.9', '36.7', '63.3', '77.8', '22.2', '46.2', '53.8']
NOP NOP vs. SAS 04/15/2015 W 48 88.0 12.0 70.4 14.8 13.9 8.3 15.7 13.9 55.6 52.6 47.4 60.0 40.0 53.5 46.5
['NOP', 'NOP', 'vs.', 'SAS', '04/15/2015', 'W', '48', '88.0', '12.0', '70.4', '14.8', '13.9', '8.3', '15.7', '13.9', '55.6', '52.6', '47.4', '60.0', '40.0', '53.5', '46.5']
NYK NYK vs. DET 04/15/2015 L 48 75.3 24.7 57.8 17.8 23.3 12.2 18.9 14.4 40.0 50.0 50.0 85.7 14.3 57.6 42.4
['NYK', 'NYK', 'vs.', 'DET', '04/15/2015', 'L', '48', '75.3', '24.7', '57.8', '17.8', '23.3', '12.2', '18.9', '14.4', '40.0', '50.0', '50.0', '85.7', '14.

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
MIA MIA vs. ORL 04/13/2015 W 48 88.0 12.0 72.0 6.0 9.0 8.0 19.0 15.0 66.0 50.0 50.0 100 0.0 53.8 46.2
['MIA', 'MIA', 'vs.', 'ORL', '04/13/2015', 'W', '48', '88.0', '12.0', '72.0', '6.0', '9.0', '8.0', '19.0', '15.0', '66.0', '50.0', '50.0', '100', '0.0', '53.8', '46.2']
CHI CHI @ BKN 04/13/2015 W 48 65.9 34.1 56.6 15.9 31.9 12.4 11.5 13.3 40.7 50.0 50.0 83.3 16.7 59.1 40.9
['CHI', 'CHI', '@', 'BKN', '04/13/2015', 'W', '48', '65.9', '34.1', '56.6', '15.9', '31.9', '12.4', '11.5', '13.3', '40.7', '50.0', '50.0', '83.3', '16.7', '59.1', '40.9']
HOU HOU @ CHA 04/13/2015 W 48 58.8 41.2 52.0 6.0 27.0 14.0 21.0 22.0 46.0 38.5 61.5 100 0.0 54.3 45.7
['HOU', 'HOU', '@', 'CHA', '04/13/2015', 'W', '48', '58.8', '41.2', '52.0', '6.0', '27.0', '14.0', '21.0', '22.0', '46.0', '38.5', '61.5', '100', '0.0', '54.3', '45.7']


TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
CHA CHA @ ATL 04/10/2015 L 48 63.9 36.1 55.0 20.0 30.0 1.3 15.0 6.3 35.0 63.6 36.4 87.5 12.5 70.0 30.0
['CHA', 'CHA', '@', 'ATL', '04/10/2015', 'L', '48', '63.9', '36.1', '55.0', '20.0', '30.0', '1.3', '15.0', '6.3', '35.0', '63.6', '36.4', '87.5', '12.5', '70.0', '30.0']
DAL DAL @ DEN 04/10/2015 W 58 73.4 26.6 63.9 18.1 22.9 16.0 13.2 13.9 45.8 63.0 37.0 90.9 9.1 68.4 31.6
['DAL', 'DAL', '@', 'DEN', '04/10/2015', 'W', '58', '73.4', '26.6', '63.9', '18.1', '22.9', '16.0', '13.2', '13.9', '45.8', '63.0', '37.0', '90.9', '9.1', '68.4', '31.6']
SAC SAC @ OKC 04/10/2015 L 48 70.4 29.6 54.4 9.7 26.2 17.5 19.4 9.7 44.7 42.9 57.1 77.8 22.2 51.4 48.6
['SAC', 'SAC', '@', 'OKC', '04/10/2015', 'L', '48', '70.4', '29.6', '54.4', '9.7', '26.2', '17.5', '19.4', '9.7', '44.7', '42.9', '57.1', '77.8', '22.2', '51.4', '48.6'

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
GSW GSW @ NOP 04/07/2015 L 48 76.8 23.2 66.0 12.0 27.0 12.0 7.0 14.0 54.0 57.6 42.4 66.7 33.3 59.5 40.5
['GSW', 'GSW', '@', 'NOP', '04/07/2015', 'L', '48', '76.8', '23.2', '66.0', '12.0', '27.0', '12.0', '7.0', '14.0', '54.0', '57.6', '42.4', '66.7', '33.3', '59.5', '40.5']
SAS SAS @ OKC 04/07/2015 W 48 73.0 27.0 65.5 21.2 26.5 4.4 8.0 15.0 44.2 45.9 54.1 100 0.0 57.4 42.6
['SAS', 'SAS', '@', 'OKC', '04/07/2015', 'W', '48', '73.0', '27.0', '65.5', '21.2', '26.5', '4.4', '8.0', '15.0', '44.2', '45.9', '54.1', '100', '0.0', '57.4', '42.6']
SAC SAC vs. MIN 04/07/2015 W 48 70.0 30.0 56.9 8.6 23.3 11.2 19.8 8.6 48.3 54.5 45.5 77.8 22.2 59.5 40.5
['SAC', 'SAC', 'vs.', 'MIN', '04/07/2015', 'W', '48', '70.0', '30.0', '56.9', '8.6', '23.3', '11.2', '19.8', '8.6', '48.3', '54.5', '45.5', '77.8', '22.2', '59.5', '40.5'

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
MEM MEM vs. OKC 04/03/2015 W 48 73.8 26.3 68.0 8.0 12.0 10.0 20.0 8.0 60.0 35.3 64.7 100 0.0 42.1 57.9
['MEM', 'MEM', 'vs.', 'OKC', '04/03/2015', 'W', '48', '73.8', '26.3', '68.0', '8.0', '12.0', '10.0', '20.0', '8.0', '60.0', '35.3', '64.7', '100', '0.0', '42.1', '57.9']
SAC SAC vs. NOP 04/03/2015 L 48 78.2 21.8 65.3 16.8 18.9 27.4 15.8 13.7 48.4 48.4 51.6 100 0.0 56.8 43.2
['SAC', 'SAC', 'vs.', 'NOP', '04/03/2015', 'L', '48', '78.2', '21.8', '65.3', '16.8', '18.9', '27.4', '15.8', '13.7', '48.4', '48.4', '51.6', '100', '0.0', '56.8', '43.2']
WAS WAS vs. NYK 04/03/2015 W 48 82.8 17.2 71.3 11.9 20.8 16.8 7.9 12.9 59.4 69.4 30.6 100 0.0 74.4 25.6
['WAS', 'WAS', 'vs.', 'NYK', '04/03/2015', 'W', '48', '82.8', '17.2', '71.3', '11.9', '20.8', '16.8', '7.9', '12.9', '59.4', '69.4', '30.6', '100', '0.0', '74.4', '2

...

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
GSW GSW @ MIN 11/08/2019 L 53 66.0 34.0 55.5 26.9 25.2 6.7 19.3 15.1 28.6 42.4 57.6 40.0 60.0 41.9 58.1
['GSW', 'GSW', '@', 'MIN', '11/08/2019', 'L', '53', '66.0', '34.0', '55.5', '26.9', '25.2', '6.7', '19.3', '15.1', '28.6', '42.4', '57.6', '40.0', '60.0', '41.9', '58.1']
UTA UTA vs. MIL 11/08/2019 W 48 57.1 42.9 36.9 5.8 43.7 9.7 19.4 17.5 31.1 26.3 73.7 66.7 33.3 44.1 55.9
['UTA', 'UTA', 'vs.', 'MIL', '11/08/2019', 'W', '48', '57.1', '42.9', '36.9', '5.8', '43.7', '9.7', '19.4', '17.5', '31.1', '26.3', '73.7', '66.7', '33.3', '44.1', '55.9']
LAL LAL vs. MIA 11/08/2019 W 48 64.0 36.0 67.4 10.5 25.3 4.2 7.4 11.6 56.8 71.9 28.1 87.5 12.5 75.0 25.0
['LAL', 'LAL', 'vs.', 'MIA', '11/08/2019', 'W', '48', '64.0', '36.0', '67.4', '10.5', '25.3', '4.2', '7.4', '11.6', '56.8', '71.9', '28.1', '87.5', '12.5', '75.0'

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
NOP NOP @ BKN 11/04/2019 L 48 67.0 33.0 56.0 17.6 31.2 12.8 12.8 17.6 38.4 20.0 80.0 84.6 15.4 37.5 62.5
['NOP', 'NOP', '@', 'BKN', '11/04/2019', 'L', '48', '67.0', '33.0', '56.0', '17.6', '31.2', '12.8', '12.8', '17.6', '38.4', '20.0', '80.0', '84.6', '15.4', '37.5', '62.5']
PHI PHI @ PHX 11/04/2019 L 48 67.4 32.6 53.2 23.9 35.8 7.3 11.0 17.4 29.4 34.5 65.5 84.6 15.4 50.0 50.0
['PHI', 'PHI', '@', 'PHX', '11/04/2019', 'L', '48', '67.4', '32.6', '53.2', '23.9', '35.8', '7.3', '11.0', '17.4', '29.4', '34.5', '65.5', '84.6', '15.4', '50.0', '50.0']
MEM MEM vs. HOU 11/04/2019 L 48 73.4 26.6 74.0 8.0 9.0 25.0 17.0 29.0 66.0 45.9 54.1 66.7 33.3 47.5 52.5
['MEM', 'MEM', 'vs.', 'HOU', '11/04/2019', 'L', '48', '73.4', '26.6', '74.0', '8.0', '9.0', '25.0', '17.0', '29.0', '66.0', '45.9', '54.1', '66.7', '33.3', '47.5'

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
HOU HOU @ BKN 11/01/2019 L 48 51.5 48.5 50.0 5.2 31.0 12.9 19.0 21.6 44.8 37.9 62.1 83.3 16.7 51.2 48.8
['HOU', 'HOU', '@', 'BKN', '11/01/2019', 'L', '48', '51.5', '48.5', '50.0', '5.2', '31.0', '12.9', '19.0', '21.6', '44.8', '37.9', '62.1', '83.3', '16.7', '51.2', '48.8']
DET DET @ CHI 11/01/2019 L 48 65.9 34.1 66.0 3.8 17.0 12.3 17.0 17.9 62.3 45.7 54.3 83.3 16.7 51.2 48.8
['DET', 'DET', '@', 'CHI', '11/01/2019', 'L', '48', '65.9', '34.1', '66.0', '3.8', '17.0', '12.3', '17.0', '17.9', '62.3', '45.7', '54.3', '83.3', '16.7', '51.2', '48.8']
IND IND vs. CLE 11/01/2019 W 48 71.9 28.1 66.7 11.8 14.7 17.6 18.6 9.8 54.9 44.1 55.9 100 0.0 51.3 48.7
['IND', 'IND', 'vs.', 'CLE', '11/01/2019', 'W', '48', '71.9', '28.1', '66.7', '11.8', '14.7', '17.6', '18.6', '9.8', '54.9', '44.1', '55.9', '100', '0.0', '51.3', '4

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
TOR TOR vs. ORL 10/28/2019 W 48 54.1 45.9 44.2 9.6 28.8 20.2 26.9 12.5 34.6 47.8 52.2 80.0 20.0 57.6 42.4
['TOR', 'TOR', 'vs.', 'ORL', '10/28/2019', 'W', '48', '54.1', '45.9', '44.2', '9.6', '28.8', '20.2', '26.9', '12.5', '34.6', '47.8', '52.2', '80.0', '20.0', '57.6', '42.4']
HOU HOU vs. OKC 10/28/2019 W 48 51.1 48.9 50.0 1.7 25.9 8.6 24.1 15.5 48.3 48.3 51.7 70.0 30.0 53.8 46.2
['HOU', 'HOU', 'vs.', 'OKC', '10/28/2019', 'W', '48', '51.1', '48.9', '50.0', '1.7', '25.9', '8.6', '24.1', '15.5', '48.3', '48.3', '51.7', '70.0', '30.0', '53.8', '46.2']
CHA CHA @ LAC 10/28/2019 L 48 53.0 47.0 45.8 2.1 43.8 9.4 10.4 25.0 43.8 59.1 40.9 78.6 21.4 66.7 33.3
['CHA', 'CHA', '@', 'LAC', '10/28/2019', 'L', '48', '53.0', '47.0', '45.8', '2.1', '43.8', '9.4', '10.4', '25.0', '43.8', '59.1', '40.9', '78.6', '21.4', '66.7'

TEAM MATCH UP GAME DATE W/L MIN %FGA
2PT %FGA
3PT %PTS
2PT %PTS
2PT MR %PTS
3PT %PTS
FBPS %PTS
FT %PTS
OFF TO %PTS
PITP 2FGM
%AST 2FGM
%UAST 3FGM
%AST 3FGM
%UAST FGM
%AST FGM
%UAST
NYK NYK @ BKN 10/25/2019 L 48 69.1 30.9 38.5 9.2 46.8 11.9 14.7 20.2 29.4 14.3 85.7 82.4 17.6 44.7 55.3
['NYK', 'NYK', '@', 'BKN', '10/25/2019', 'L', '48', '69.1', '30.9', '38.5', '9.2', '46.8', '11.9', '14.7', '20.2', '29.4', '14.3', '85.7', '82.4', '17.6', '44.7', '55.3']
UTA UTA @ LAL 10/25/2019 L 48 64.3 35.7 48.8 4.7 27.9 16.3 23.3 19.8 44.2 61.9 38.1 75.0 25.0 65.5 34.5
['UTA', 'UTA', '@', 'LAL', '10/25/2019', 'L', '48', '64.3', '35.7', '48.8', '4.7', '27.9', '16.3', '23.3', '19.8', '44.2', '61.9', '38.1', '75.0', '25.0', '65.5', '34.5']
DEN DEN vs. PHX 10/25/2019 W 53 70.7 29.3 53.7 9.3 19.4 13.0 26.9 21.3 44.4 51.7 48.3 85.7 14.3 58.3 41.7
['DEN', 'DEN', 'vs.', 'PHX', '10/25/2019', 'W', '53', '70.7', '29.3', '53.7', '9.3', '19.4', '13.0', '26.9', '21.3', '44.4', '51.7', '48.3', '85.7', '14.3', '58.3'